# An Expected Goals model in Julia

Here's what this notebook is *not* - 
+ It's *not* a definitive guide to expected goals. If that's what you want, check out [this](https://github.com/ML-KULeuven/soccer_xg), [this](https://youtu.be/310_eW0hUqQ), and [this](http://petermckeever.com/2019/01/building-an-expected-goals-model-in-python/)

+ It's not a full-fledged tutorial for Julia. For that, check out [this](https://youtu.be/sE67bP2PnOo) tutorial by Derek Banas. 

Guess, this is somewhere in the middle of both - applying Julia basics to build an expected goals model (AKA xG model)

**Enough talk, let's code!**

## Installing packages

Python has **pip**, Julia has **Pkg**. We're gonna need 6 packages for our xg model (find the names from the first code section below). It's relatively straightforward to install packages in Julia. I'm assuming you already have Julia installed and added to path. The steps to install any package are as follows:

1. Open a terminal and type in `julia` and hit enter. That should open up the julia REPL for you (within the same shell). 
2. Enter `using Pkg`. That should open the Pkg REPL within the shell itself.
3. To install any package, just use `add`: `Pkg.add("the_package_name")`. For example, to install `Plots`, enter `Pkg.add("Plots")`. 


## Imports

Imports usually work using the `using` keyword. It's kinda like a wildcard (\*) import in Python insomuch as you get all the methods, variables, structs in one go. There's also the `import` statement and, indeed, a few other ways to import external modules (check out the relevant section [here](https://docs.julialang.org/en/v1/manual/modules/index.html#Summary-of-module-usage-1)). However, the using is the most common way I've seen so we'll stick with that. 

In [7]:
using DataFrames, CSV
using XGBoost
using LinearAlgebra
using Random
using Plots

┌ Info: Precompiling MLJ [add582a8-e3ab-11e8-2d5e-e98b27df1bc7]
└ @ Base loading.jl:1192
[ Info: Model metadata loaded from registry. 


## Data

The shots data is from [here](https://raw.githubusercontent.com/sharmaabhishekk/undershot_backup/master/understat_all_shots.csv). I have it downloaded in the same directory as `shots.csv` so you should do the same to follow along. It's basically all shots from the 2014 season to 2018 for all top 5 leagues plus the Russian Premier League. So that's basically 30 seasons long shots data. More than enough for our needs!

In [8]:
df = DataFrame!(CSV.File("shots.csv"))
first(df, 5)
##show(df,allcols=true) ##for checking all column names

5×20 DataFrame. Omitted printing of 15 columns
│ Row │ X       │ Y       │ a_goals │ a_team        │ date             │
│     │ Float64 │ Float64 │ Int64   │ String        │ String           │
├─────┼─────────┼─────────┼─────────┼───────────────┼──────────────────┤
│ 1   │ 0.707   │ 0.379   │ 0       │ Hoffenheim    │ 29-08-2015 17:30 │
│ 2   │ 0.728   │ 0.373   │ 1       │ Darmstadt     │ 12-09-2015 17:30 │
│ 3   │ 0.016   │ 0.464   │ 0       │ Darmstadt     │ 01-11-2015 18:30 │
│ 4   │ 0.875   │ 0.521   │ 2       │ Darmstadt     │ 20-12-2015 20:30 │
│ 5   │ 0.927   │ 0.557   │ 2       │ Werder Bremen │ 07-12-2014 16:30 │

The data is in a `Dataframe`. You can explore the data a little - in fact, that's probably a must. But here's some important stuff to know:

1. Shot coordinates are in the **(0,1) range** on both axes: x and y. 
2. We have the preceding action to a shot (dribble/pass/throughball whatever) in a column called `lastAction`. We also have the situation of the shot (open-play/corner/direct-freekick/penalty `situation`. 

Our preprocessing steps are gonna look like this:

+ Remove all own-goals. 
+ For simplicity, we'll only consider open-play shots so remove all deadball situations (corners, freekicks, pens)
+ Remove all shots which are not taken from the foot or head.
+ Calculate the goalmouth angle and distance for each shot

+ Encode data to integers


## Getting the features

We are gonna use **xgboost** as the classifer for our expected goals model. We're gonna need to decide on what features to use to train the model. I decided to go with **shot location**, **goalmouth angle** (*how much of the goal can the player see*), **distance** (*distance between the shot location and the goal*). Why these? Check out this excellent [blog post](https://dtai.cs.kuleuven.be/sports/blog/illustrating-the-interplay-between-features-and-models-in-xg) from the good folks over at KU Leuven. Basically, they found that the best features would be the **shot location**, **angle**, **distance**, and the **product of the angle and distance**. I skipped the last feature because this was just a test run anyway but feel free to add it in. 

We already have the (x,y) location. All we need is to calculate the angle and distance (we do that in the next few lines of code).

In [9]:
square(n) = n * n ##this is a function (we're gonna need it to calculate the length)
get_angle(px, py) = atan(.55 - py, 1 - px) - atan(.45 - py, 1 - px) ##another function which we're gonna need to calculate the angle (https://stackoverflow.com/a/31334882)

df = df[((df[:, "result"] .!= "OwnGoal") .& (df[:, "shotType"] .!= "OtherBodyPart") .& (df[:, "situation"] .== "OpenPlay")), :]; 
##remove owngoals, remove otherbodypart, keep only openplay shots

df[!, :goal_mid_x] .= 1
df[!, :goal_mid_y] .= .5
df[!, "length"] = .√( map(square, (df["goal_mid_x"] .- df["X"])) + map(square, (df["goal_mid_y"] .- df["Y"])) ) ##simple distance formula for two points
df[!, "angle"] = map(get_angle, df.X, df.Y);

┌ Warning: `getindex(df::DataFrame, col_ind::ColumnIndex)` is deprecated, use `df[!, col_ind]` instead.
│   caller = top-level scope at In[9]:7
└ @ Core In[9]:7
┌ Warning: `getindex(df::DataFrame, col_ind::ColumnIndex)` is deprecated, use `df[!, col_ind]` instead.
│   caller = top-level scope at In[9]:7
└ @ Core In[9]:7
┌ Warning: `getindex(df::DataFrame, col_ind::ColumnIndex)` is deprecated, use `df[!, col_ind]` instead.
│   caller = top-level scope at In[9]:7
└ @ Core In[9]:7
┌ Warning: `getindex(df::DataFrame, col_ind::ColumnIndex)` is deprecated, use `df[!, col_ind]` instead.
│   caller = top-level scope at In[9]:7
└ @ Core In[9]:7


Okay so a few remarks on what happened above. 

+ Julia functions can be defined in many different ways. The two functions above - `square` & `get_angle` defined in what's called the "**assignment format**". You can also use the `function` keyword to do it. You can even have multiple functions with the same name but different argument signatures! Very cool stuff.

+ The exclamation mark in the `df` is basically just saying "*select all rows*". It's similar to slicing dataframes in pandas, where we use the colon (:) to do what (!) does here.

+ The dot `.` before any operator like `+`,`-`,`*` means that the operation is to be **vectorized**. Basically to add two arrays, you'd use `.+`. To assign a value to an entire column, we'd use `.=` and so on. Docs [here](https://docs.julialang.org/en/v1/manual/mathematical-operations/#man-dot-operators-1)

+ You might have also noticed the `√` symbol. It's basically the square root (doh). Julia supports a lot of those symbols (α, β, ϵ, δ, π, λ, and tons more). Even emojis.

😊😃😏😍😘😚😳😌😆


## Encoding the data

We have the features in the dataframe `df` now. The next step is to encode the categorical data so that we can pass it to the XGBoost DMatrix. In Python, I use dictionaries to do this. Thankfully, they also exist in Julia. The next section first creates the dictionary and then creates a new column in `df` to encode in the data. 

In [10]:
result_dict = Dict{String,Int32}("MissedShots" => 0, 
                    "OwnGoal" => 0,
                    "SavedShot" => 0,
                    "Goal" => 1, 
                    "BlockedShot" => 0,
                    "ShotOnPost" => 0)

body_part_dict = Dict{String,Int32}("RightFoot" => 1, 
                    "OtherBodyPart" => 0,
                    "LeftFoot" => 1,
                    "Head" => 0);

In [11]:
df[!, "result_int"] = map(key->result_dict[key], df.result)
df[!, "body_part_int"] = map(k->body_part_dict[k], df.shotType);

## Training the model

That's about all the preprocessing we need. The next step is to shuffle the data randomly (a case can also be made to train the data of certain leagues or certain seasons)
and then test on certain others. I've tried that and there's not much difference so I prefer to shuffle everything anyway. 

Anyway, in the next cells we split the data, then convert everything we need to an array and throw it in the classifer. 

In [12]:
function partitionTrainTest(data, at = 0.7)
    ##https://discourse.julialang.org/t/simple-tool-for-train-test-split/473/3
    n = nrow(data)
    idx = shuffle(1:n)
    train_idx = view(idx, 1:floor(Int, at*n))
    test_idx = view(idx, (floor(Int, at*n)+1):n)
    data[train_idx,:], data[test_idx,:]
end

train, test = partitionTrainTest(df, 0.85);

In [25]:
num_rounds = 400

train_X = convert(Array{Float32}, train[!, [:X, :Y, :length, :angle, :body_part_int]])
train_y = convert(Array{Float32}, train[!, :result_int])

test_X = convert(Array{Float32}, test[!, [:X, :Y, :length, :angle, :body_part_int]])
test_y = convert(Array{Float32}, test[!, :result_int])

dtrain = DMatrix(train_X, label=train_y)
model = xgboost(dtrain, num_rounds); ##default loss metric is RMSE

y_predictions = XGBoost.predict(model, test_X);


[1]	train-rmse:0.401894
[2]	train-rmse:0.343644
[3]	train-rmse:0.311020
[4]	train-rmse:0.293630
[5]	train-rmse:0.284629
[6]	train-rmse:0.280051
[7]	train-rmse:0.277707
[8]	train-rmse:0.276437
[9]	train-rmse:0.275751
[10]	train-rmse:0.275412
[11]	train-rmse:0.275176
[12]	train-rmse:0.274963
[13]	train-rmse:0.274803
[14]	train-rmse:0.274706
[15]	train-rmse:0.274572
[16]	train-rmse:0.274482
[17]	train-rmse:0.274339
[18]	train-rmse:0.274267
[19]	train-rmse:0.274195
[20]	train-rmse:0.274165
[21]	train-rmse:0.274107
[22]	train-rmse:0.273994
[23]	train-rmse:0.273822
[24]	train-rmse:0.273709
[25]	train-rmse:0.273667
[26]	train-rmse:0.273541
[27]	train-rmse:0.273468
[28]	train-rmse:0.273394
[29]	train-rmse:0.273362
[30]	train-rmse:0.273229
[31]	train-rmse:0.273119
[32]	train-rmse:0.273042
[33]	train-rmse:0.272982
[34]	train-rmse:0.272852
[35]	train-rmse:0.272745
[36]	train-rmse:0.272600
[37]	train-rmse:0.272483
[38]	train-rmse:0.272349
[39]	train-rmse:0.272227
[40]	train-rmse:0.272155
[41]	trai

29010-element Array{Float32,1}:
  0.008194774 
  0.025120169 
  0.10851312  
  0.014182031 
  0.17673767  
  0.020157844 
 -0.0011060834
  0.061106145 
  0.022949219 
  0.06375396  
  0.021404117 
  0.096826315 
  0.2340616   
  ⋮           
  0.02625975  
  0.06015557  
  0.03600073  
  0.064156234 
  0.021899104 
  0.19360062  
  0.05744317  
  0.0030175745
  0.05725217  
  0.102924794 
  0.019626588 
  0.043044627 

## Plotting the data

To be honest, I haven't gotten very familiar with the plotting features available. A heatmap or contourmap would've been ideal for this but I don't know yet how to do those so I'll stick to just plotting the shots on a pitch with their colors being their predicted xg values and then we'll see if that looks intuitive. 

In [31]:
function arc(h, k, r, α=0, β=2*π) 
   """ returns points on the full circumference of a circle""" 
   θ = LinRange(α, β, 500) 
   h .+ r*sin.(θ), k .+ r*cos.(θ) ##the circle equation 
end 

x1 = [0, 120, 120, 0, 0]; y1 = [0, 0, 80, 80, 0] ## pitch outlines 
x2 = [0, 18, 18, 0, 0]; y2 = [18, 18, 62, 62, 18] ## left d-box 
x3 = [102, 120, 120, 102, 102]; y3 = [18, 18, 62, 62, 18] ## right d-box 
x4 = [0, 6, 6, 0, 0]; y4 = [30, 30, 50, 50, 30] ## left 6-yard box 
x5 = [114, 120, 120, 114, 114]; y5 = [30, 30, 50, 50, 30] ## right 6-yard box 

##goals 
x6 = [0,0]; y6 = [36, 44] 
x7 = [120, 120]; y7=y6 

##halfway line and penalty spots 
x8 = [60,60]; y8 = [0,80] 

plot(x1, y1, color=:red) 
plot!(x2, y2, color=:red)  ##plot! basically means to modify the existing plot itself. If you remove the '!', it would overwrite the previous graphic
plot!(x3, y3, color=:red) 
plot!(x4, y4, color=:red) 
plot!(x5, y5, color=:red) 
plot!(x6, y6, color=:red, lw=4) 
plot!(x7, y7, color=:red, lw=4) 
plot!(x8, y8, color=:red) 
plot!(xlim=(-1, 121), ylim=(-1, 81), legend=false, grid=false, border=:none) 
scatter!([12, 60, 108], [40, 40, 40], color=:red) 

plot!(arc(60, 40, 8.5), seriestype = [:shape,], lw = 0.5, linecolor = :red, fillalpha = 0.01, aspect_ratio = 1) 

### 

function plot_arcs(type) 
   θs = LinRange(0, 2π, 100) ##100 points from 0 to 6.283..
   radius = 9 
   xs = radius*cos.(θs) 
   ys = radius*sin.(θs) 
                        
   if (type == "corners")

       x_conds = [xs.>=0, xs.<=120, xs.<=120, xs.>=0] ##the conditionals for the plotting of the corner arcs
       y_conds = [ys.>=0, ys.>=0, ys.<=80, ys.<=80] ##the y conditionals for the same
       x_offsets = [0, 120, 120, 0]
       y_offsets = [0, 0, 80, 80]

       for (xcond, ycond, xoff, yoff) in zip(x_conds, y_conds, x_offsets, y_offsets)
           radius = 2
           xs = radius*cos.(θs) 
           ys = radius*sin.(θs) 

           xs = xs .+ xoff    
           ys = ys .+ yoff 
           final = (xcond) .& (ycond)
           xh = xs[1:end-1] 
           yh = ys[1:end-1] 

           plot!(xh, yh, color = :red)
       end    

   

   elseif(type == "left")     
           xs = xs .+ 12     
           ys = ys .+ 40; 
           cond = xs.>=18 
           xh = xs[findall(cond)] 
           yh = ys[findall(cond)] 
           plot!(xh, yh, color = :red) 
                
   elseif(type == "right") 
           xs = xs .+ 108     
           ys = ys .+ 40; 
           cond = xs.<=102 
           xh = xs[findall(cond)] 
           yh = ys[findall(cond)] 
           plot!(xh, yh, color = :red) 
   end 
end

plot_arcs("right") 
plot_arcs("left") 
plot_arcs("corners")
                
scatter!(map(round, test_X[:, 1]*120), map(round, test_X[:, 2]*80), marker_z = map(round, y_predictions*100), ##weird rounding hack to give the impression of a grid
                    markersize=1.5, legend=nothing, color=:jet, markerstrokewidth=.4, dpi=105, alpha=.5) ##increase the dpi a little for higher quality image
##png("final_jl_2") ## to save the image

## Final thoughts

It does look right to me. The most obvious limitation is that I haven't validated the model, at all. The truth is I haven't been able to get it working alright in Julia. If I can't, I might use `PyCall` to use `sklearn`'s `brier_score`. What metric to use? The *Brier score* is what the guys over at KU Leuven suggest. 

+ Also I noticed how some the xg values of some shots wider out aren't as close to 0.0 as I'd like them to be. There's something definitely off there. Perhaps that extra feature (the product of length and angle(θ)) might help with that. 

+ You'd probably also want to add more features. There is a lot of information within this dataset itself which I have thrown away which might help to further refine the model. At any rate, it looks like a decent starting point so I'm happy to put it out, as is.